In [1]:
# TENSORFLOW CHECK
"""
# What version of Python do you have?
import sys

import tensorflow.keras
import pandas as pd
import sklearn as sk
import tensorflow as tf

print(f"Tensor Flow Version: {tf.__version__}")
print(f"Keras Version: {tensorflow.keras.__version__}")
print()
print(f"Python {sys.version}")
print(f"Pandas {pd.__version__}")
print(f"Scikit-Learn {sk.__version__}")
gpu = len(tf.config.list_physical_devices('GPU'))>0
print("GPU is", "available" if gpu else "NOT AVAILABLE")
"""

'\n# What version of Python do you have?\nimport sys\n\nimport tensorflow.keras\nimport pandas as pd\nimport sklearn as sk\nimport tensorflow as tf\n\nprint(f"Tensor Flow Version: {tf.__version__}")\nprint(f"Keras Version: {tensorflow.keras.__version__}")\nprint()\nprint(f"Python {sys.version}")\nprint(f"Pandas {pd.__version__}")\nprint(f"Scikit-Learn {sk.__version__}")\ngpu = len(tf.config.list_physical_devices(\'GPU\'))>0\nprint("GPU is", "available" if gpu else "NOT AVAILABLE")\n'

In [6]:
# RUN THE FILES IF THEY HAVEN'T
!python3 minesweeper.py
!python3 DQNsetup.py
# from minesweeper_env import *
import random
import numpy as np
import pandas as pd
import math
import minesweeper
from minesweeper import Board
import DQNsetup
from DQNsetup import *
from collections import deque
from tqdm import tqdm

Init Plugin
Init Graph Optimizer
Init Kernel


In [3]:
# Environment settings
MEM_SIZE = 50_000 # number of moves to store in replay buffer
MEM_SIZE_MIN = 40 # min number of moves in replay buffer
episodes = 100

# Learning settings
BATCH_SIZE = 10
learn_rate = 0.001
LEARN_DECAY = 0.99975
LEARN_MIN = 0.001
DISCOUNT = 0.1 #gamma

# Exploration settings
epsilon = 0.95
EPSILON_DECAY = 0.99975
EPSILON_MIN = 0.01

# DQN settings
CONV_UNITS = 64 # number of neurons in each conv layer
DENSE_UNITS = 512 # number of neurons in fully connected dense layer
UPDATE_TARGET_EVERY = 5

In [4]:
# INITIALIZING EVERTHING CELL

# Initialize the Board (4x4 matrix)
env = Board(9, 9)

# Set the mines about (2,2)
# Assume user clicked coordinate (2,2) as the first tile
f_row, f_col = np.random.randint(env.rows, size=2)
print("First row: %d, First Col: %d" % (f_row, f_col))
env.set_mines_about(f_row, f_col,10) # set_mines_about(self,row_center,col_center,num_mines)
print("Mines: ")
env.printMines()
print("Board: ")
env.printBoard()
state_im = env.board3D() # board is currently 2D, making it 3D by (row, col, 1)

# Initialize the model 
model = DQN_setup(learn_rate, state_im.shape, env.ntiles, CONV_UNITS, DENSE_UNITS)

# Initialize the model that would always be ahead (looking at the future)
target_model = DQN_setup(learn_rate, state_im.shape, env.ntiles, CONV_UNITS, DENSE_UNITS)
target_model.set_weights(model.get_weights())

replay_memory = deque(maxlen=MEM_SIZE)
target_update_counter = 0

2022-01-10 01:28:02.872949: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2022-01-10 01:28:02.873095: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


First row: 0, First Col: 7
Opening ( 0, 7 ) ...
Opening ( 0, 6 ) ...
Opening ( 0, 5 ) ...
Opening ( 0, 4 ) ...
Progressed ...
Opening ( 1, 4 ) ...
Progressed ...
Opening ( 1, 5 ) ...
Opening ( 1, 6 ) ...
Opening ( 1, 7 ) ...
Progressed ...
Opening ( 2, 5 ) ...
Progressed ...
Opening ( 2, 6 ) ...
Progressed ...
Opening ( 2, 7 ) ...
Progressed ...
Progressed ...
Opening ( 2, 4 ) ...
Progressed ...
Progressed ...
Progressed ...
Progressed ...
Opening ( 0, 8 ) ...
Opening ( 1, 8 ) ...
Progressed ...
Progressed ...
Progressed ...
Mines: 
[[0 0 0 1 0 0 0 0 0]
 [0 1 0 0 0 0 0 0 0]
 [0 1 1 0 0 0 0 0 1]
 [0 0 0 0 0 1 0 1 0]
 [0 0 0 0 0 0 0 0 1]
 [0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 1]
 [0 0 0 0 1 0 0 0 0]]
Board: 
[[-8. -8. -8. -8.  1.  0.  0.  0.  0.]
 [-8. -8. -8. -8.  1.  0.  0.  1.  1.]
 [-8. -8. -8. -8.  1.  1.  2.  2. -8.]
 [-8. -8. -8. -8. -8. -8. -8. -8. -8.]
 [-8. -8. -8. -8. -8. -8. -8. -8. -8.]
 [-8. -8. -8. -8. -8. -8. -8. -8. -8.]
 [-8. -8. -8. -8. -8. -8. -8.

In [5]:
# PLAY THE GAME!!! (# episodes Games)
for episode in tqdm(range(1,episodes+1), unit='episode'):
    env.reset()
    f_row, f_col = np.random.randint(env.rows, size=2)
    env.set_mines_about(f_row, f_col,15)
    done = False
    ep_reward = 0

    # play until lose
    while not done:
        # get action
        board = env.board3D().reshape(1, env.ntiles)
        print("Board: ", board)

        # Select the unopened tiles
        unopened_tiles = [i for i, value in enumerate(board[0]) if value==-1]
        print("Unopened Tiles: ", unopened_tiles)

        rand = np.random.random() # number from 0 to 1

        if rand < epsilon:
            print("\nUsed Random")
            move = np.random.choice(unopened_tiles)
        else:
            print("\nUsed Model To Predict")
            moves = model.predict(np.reshape(state_im, (1, env.rows, env.cols, 1)))
            print(type(moves))
            print("moves:", moves)
            # Disregard all the opened tiles
            moves[board!=-1] = np.min(moves)
            # Pick a tile with the best probability
            move = np.argmax(moves)


        print("\naction: ", move)
        print("Board: ", env.board)
        print("Mines: ", env.mines)

        # Retrieve the next step and reward
        new_state, reward, done = env.dig(math.floor(move / env.cols), move % env.cols)
        print("\nREWARD: ", reward)
        ep_reward += reward

        # append the data to batch_array
        current_state = env.board3D()
        replay_memory.append((current_state, move, reward, new_state, done))

        # Train
        if len(replay_memory) < MEM_SIZE_MIN:
            print("SKIP")
            continue

        # Get the random sample of batches
        batch = random.sample(replay_memory, BATCH_SIZE)

        # Q table for current model using the batches
        current_states = np.array([transition[0] for transition in batch])
        current_qs_list = model.predict(current_states)
        print(current_qs_list.shape)
        print("\nCurrent Q Table: ", current_qs_list)

        # Q table for future model
        new_current_states = np.array([transition[3] for transition in batch])
        future_qs_list = target_model.predict(new_current_states)
        print(future_qs_list.shape)
        print("\nFuture Q Table: ", future_qs_list)
        
        X_train = [] # Feature
        Y_train = [] # Label

        for i, (current_state, action, reward, new_current_states, done) in enumerate(batch):
            if not done:
                max_future_q = np.max(future_qs_list[i])
                new_q = reward + DISCOUNT * max_future_q
            else:
                new_q = reward

            current_qs = current_qs_list[i]
            current_qs[action] = new_q

            X_train.append(current_state)
            Y_train.append(current_qs)

        model.fit(np.array(X_train), np.array(Y_train), batch_size=BATCH_SIZE)

        # updating to determine if we want to update target_model yet
        if done:
            target_update_counter += 1

        if target_update_counter > UPDATE_TARGET_EVERY:
            target_model.set_weights(model.get_weights())
            target_update_counter = 0

        # decay learn_rate
        learn_rate = max(LEARN_MIN, learn_rate*LEARN_DECAY)

        # decay epsilon
        epsilon = max(EPSILON_MIN, epsilon*EPSILON_DECAY)
    print("Episode Reward: ", ep_reward)
print("Number of Wins :", env.n_wins)
model.save("model_9x9_10B")

  0%|                                                                        | 0/100 [00:00<?, ?episode/s]

Opening ( 2, 5 ) ...
Opening ( 1, 4 ) ...
Opening ( 0, 3 ) ...
Progressed ...
Opening ( 0, 4 ) ...
Opening ( 0, 5 ) ...
Opening ( 0, 6 ) ...
Progressed ...
Opening ( 1, 5 ) ...
Opening ( 1, 6 ) ...
Progressed ...
Opening ( 2, 4 ) ...
Opening ( 1, 3 ) ...
Progressed ...
Opening ( 2, 3 ) ...
Progressed ...
Opening ( 3, 3 ) ...
Progressed ...
Opening ( 3, 4 ) ...
Opening ( 3, 5 ) ...
Progressed ...
Opening ( 4, 3 ) ...
Progressed ...
Opening ( 4, 4 ) ...
Opening ( 4, 5 ) ...
Progressed ...
Opening ( 5, 3 ) ...
Progressed ...
Opening ( 5, 4 ) ...
Progressed ...
Opening ( 5, 5 ) ...
Progressed ...
Progressed ...
Progressed ...
Progressed ...
Opening ( 2, 6 ) ...
Progressed ...
Progressed ...
Progressed ...
Progressed ...
Progressed ...
Opening ( 3, 6 ) ...


2022-01-10 01:28:03.113833: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:176] None of the MLIR Optimization Passes are enabled (registered 2)
2022-01-10 01:28:03.116426: W tensorflow/core/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz
2022-01-10 01:28:03.162372: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:112] Plugin optimizer for device_type GPU is enabled.
  8%|█████                                                           | 8/100 [00:00<00:01, 56.41episode/s]

Progressed ...
Progressed ...
Board:  [[-1.    -1.    -1.     0.125  0.     0.     0.125 -1.    -1.    -1.
  -1.    -1.     0.125  0.     0.     0.125 -1.    -1.    -1.    -1.
  -1.     0.25   0.     0.     0.125 -1.    -1.    -1.    -1.    -1.
   0.125  0.     0.125  0.125 -1.    -1.    -1.    -1.    -1.     0.125
   0.     0.125 -1.    -1.    -1.    -1.    -1.    -1.     0.25   0.25
   0.375 -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.
  -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.
  -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.    -1.
  -1.   ]]
Unopened Tiles:  [0, 1, 2, 7, 8, 9, 10, 11, 16, 17, 18, 19, 20, 25, 26, 27, 28, 29, 34, 35, 36, 37, 38, 42, 43, 44, 45, 46, 47, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80]

Used Random

action:  54
Board:  [[-1.    -1.    -1.     0.125  0.     0.     0.125 -1.    -1.   ]
 [-1.    -1.    -1.     0.125  0.     0.     0

(10, 81)

Current Q Table:  [[-0.0423541   0.02564935 -0.00861103 -0.01449639 -0.0302288   0.05926542
   0.02558112  0.00494518  0.0607663  -0.00029164 -0.01085255  0.00461826
  -0.04331583 -0.0457476  -0.02205717 -0.05061489 -0.04441883 -0.03928411
   0.02629797 -0.01794862 -0.02498418  0.04298703 -0.00366697 -0.04211636
  -0.03144282  0.01643717 -0.01348529  0.02786828 -0.03605992 -0.02174871
   0.03535527 -0.00177448  0.05818752 -0.01184837  0.00931249  0.02375559
   0.00197502 -0.03875647 -0.00725929  0.04592894 -0.01840604  0.02343125
   0.01075555 -0.00829347 -0.00899875  0.00260328  0.00345103  0.0038032
   0.0048639   0.06589818 -0.03916104  0.00147971 -0.0321478  -0.03403692
  -0.02240131 -0.00336864  0.00390678 -0.0078252  -0.03027879  0.04000095
  -0.00446093  0.01206627  0.02160068  0.0667429   0.02996254  0.02372074
  -0.0224852  -0.02827736 -0.00963441 -0.02267087  0.01377237 -0.0059516
  -0.00454112 -0.00471236 -0.05850781 -0.01007742 -0.03127458  0.02209771
  -0.0466755

...

100%|██████████████████████████████████████████████████████████████| 100/100 [00:20<00:00,  4.76episode/s]

Episode Reward:  -3.4
Number of Wins : 0



2022-01-10 01:28:24.177296: W tensorflow/python/util/util.cc:348] Sets are not currently considered sequences, but this may change in the future, so consider avoiding using them.


INFO:tensorflow:Assets written to: model_9x9_10B/assets


INFO:tensorflow:Assets written to: model_9x9_10B/assets
